## <span style="color:teal"> __BRAY-CURTIS DISTANCE CALCULATION__

<span style="color:teal"> **Bray–Curtis diversity analysis** is a widely used method in ecological and microbiome studies to quantify the compositional dissimilarity between two samples based on counts or relative abundances of taxa. Unlike measures that consider only the presence or absence of species (like Jaccard), Bray–Curtis takes abundance into account, making it sensitive to both shared taxa and their relative representation. The Bray–Curtis dissimilarity score ranges from 0 to 1, where 0 indicates that two samples have identical compositions, and 1 indicates complete dissimilarity (no shared taxa). This measure is particularly useful in microbiome studies to evaluate how different microbial communities are between health and disease states, across treatment conditions, or between environments. When paired with ordination methods such as Principal Coordinates Analysis (PCoA), Bray–Curtis enables visual exploration of patterns in microbial community structure, helping researchers identify clustering, gradients, or outliers that may reflect underlying biological or environmental factors.

The **Bray–Curtis dissimilarity** between two samples $A$ and $B$ is given by the formula:

$$
\text{Bray–Curtis}(A, B) = \frac{\sum_{i=1}^{S} |a_i - b_i|}{\sum_{i=1}^{S} (a_i + b_i)}
$$

### Where:

* $S$ is the total number of species (or taxa),
* $a_i$ is the abundance of species $i$ in sample $A$,
* $b_i$ is the abundance of species $i$ in sample $B$,
* $|a_i - b_i|$ is the absolute difference in abundance of species $i$ between the two samples.

### Interpretation:

* The numerator is the **sum of absolute differences** in species abundances,
* The denominator is the **total combined abundance** across both samples,
* The result ranges from **0** (identical communities) to **1** (completely different communities, no shared species).

This formula assumes **non-negative values**, such as counts or relative abundances, and is **not sensitive to double zeros** (i.e., species absent in both samples are ignored), which makes it especially suitable for ecological data.
____


In [15]:
# LOADING PACKAGES
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from skbio.diversity import beta_diversity
from skbio.stats.ordination import pcoa
from scipy.spatial import procrustes
import tqdm
from skbio.stats.distance import permanova
from joblib import Parallel, delayed
import os
import multiprocessing
from statsmodels.stats.multitest import multipletests
import warnings
warnings.filterwarnings("ignore", message="The result contains negative eigenvalues.*")


In [16]:
df_genus= pd.read_csv('/mnt/iusers01/fatpou01/bmh01/msc-bioinf-2024-2025/h44063jg/gmrepo_curated_data/disease_genus_abundance.txt', sep = '\t')
df_species= pd.read_csv('/mnt/iusers01/fatpou01/bmh01/msc-bioinf-2024-2025/h44063jg/gmrepo_curated_data/disease_species_abundance.txt', sep = '\t')

____

In [17]:
# Step 1: Exclude unknown taxa
df_genus_clean = df_genus[df_genus["ncbi_taxon_id"] != -1]

# Step 2: Keep only diseases with ≥ 30 samples
sample_counts = df_genus_clean.groupby("disease")["loaded_uid"].nunique()
eligible_diseases = sample_counts[sample_counts >= 30].index.tolist()

df_genus_filtered = df_genus_clean[df_genus_clean["disease"].isin(eligible_diseases)]

# Step 3: Count disease vs healthy samples
healthy_code = 'D006262'

num_healthy_samples = df_genus_filtered[df_genus_filtered["disease"] == healthy_code]["loaded_uid"].nunique()
num_disease_samples = df_genus_filtered[df_genus_filtered["disease"] != healthy_code]["loaded_uid"].nunique()

# Final summary
num_diseases = df_genus_filtered["disease"].nunique()
num_samples = df_genus_filtered["loaded_uid"].nunique()
num_taxa = df_genus_filtered["ncbi_taxon_id"].nunique()

# Print
print(f"✅ Summary after filtering:")
print(f"- Unique diseases: {num_diseases}")
print(f"- Unique samples (loaded_uid): {num_samples}")
print(f"- Unique taxa (ncbi_taxon_id): {num_taxa}")
print(f"- Healthy samples (D006262): {num_healthy_samples}")
print(f"- Disease samples (excluding healthy): {num_disease_samples}")

# Optional: return the filtered DataFrame
df_genus_filtered


✅ Summary after filtering:
- Unique diseases: 66
- Unique samples (loaded_uid): 26618
- Unique taxa (ncbi_taxon_id): 1710
- Healthy samples (D006262): 12485
- Disease samples (excluding healthy): 14152


loaded_uid  ncbi_taxon_id  relative_abundance  disease
1                 1            469             0.06862  D006262
2                 1            544             5.55281  D006262
3                 1            561            28.70520  D006262
4                 1            570             0.53268  D006262
5                 1            816            42.06320  D006262
...             ...            ...                 ...      ...
2295609       52859         207244             1.38735  D003093
2295610       52859         216851             0.75876  D003093
2295611       52859         239934             0.00057  D003093
2295612       52859         543311             0.00317  D003093
2295613       52859         572511            30.71760  D003093

[2249445 rows x 4 columns]

In [18]:
# Check for duplicates across disease, loaded_uid, and ncbi_taxon_id

duplicates_genus = df_genus_filtered.duplicated(subset=["disease", "loaded_uid", "ncbi_taxon_id"])

# Count how many duplicates exist
num_duplicates_genus = duplicates_genus.sum()

# Display summary
if num_duplicates_genus > 0:
    print(f"Found {num_duplicates_genus} duplicate rows based on (disease, loaded_uid, ncbi_taxon_id).")
    display(df_genus_filtered[duplicates].head())
else:
    print("No duplicates found for (disease, loaded_uid, ncbi_taxon_id).")


No duplicates found for (disease, loaded_uid, ncbi_taxon_id).


In [19]:
# PIVOT THE TABLE FOR BRAY-CURTIS DISTANCE CALCULATION
# Step 1: Pivot to sample-by-taxon matrix
df_genus_pivot = (
    df_genus_filtered
    .pivot_table(
        index=["disease", "loaded_uid"],
        columns="ncbi_taxon_id",
        values="relative_abundance",
        aggfunc="sum",
        fill_value=0
    )
)
df_genus_pivot

ncbi_taxon_id          6        10       13       16        18        20       \
disease    loaded_uid                                                           
D000067011 31059           0.0      0.0      0.0      0.0  0.000000  0.000000   
           31060           0.0      0.0      0.0      0.0  0.014162  0.036585   
           31061           0.0      0.0      0.0      0.0  0.000000  0.000000   
           31062           0.0      0.0      0.0      0.0  0.000000  0.000000   
           31063           0.0      0.0      0.0      0.0  0.000000  0.000000   
...                        ...      ...      ...      ...       ...       ...   
D065626    39893           0.0      0.0      0.0      0.0  0.000000  0.000000   
           39894           0.0      0.0      0.0      0.0  0.000000  0.000000   
           39895           0.0      0.0      0.0      0.0  0.000000  0.000000   
           39896           0.0      0.0      0.0      0.0  0.000000  0.000000   
           47572           0.0      0.0      0.0      0.0  0.000000  0.000000   

ncbi_taxon_id           22       32       40       42       ...  2211641  \
disease    loaded_uid                                       ...            
D000067011 31059       0.009302      0.0      0.0      0.0  ...      0.0   
           31060       0.000000      0.0      0.0      0.0  ...      0.0   
           31061       0.013244      0.0      0.0      0.0  ...      0.0   
           31062       0.001709      0.0      0.0      0.0  ...      0.0   
           31063       0.003956      0.0      0.0      0.0  ...      0.0   
...                         ...      ...      ...      ...  ...      ...   
D065626    39893       0.000000      0.0      0.0      0.0  ...      0.0   
           39894       0.000000      0.0      0.0      0.0  ...      0.0   
           39895       0.000000      0.0      0.0      0.0  ...      0.0   
           39896       0.000000      0.0      0.0      0.0  ...      0.0   
           47572       0.064881      0.0      0.0      0.0  ...      0.0   

ncbi_taxon_id          2212691  2212731  2282523   2282740  2282741   2282742  \
disease    loaded_uid                                                           
D000067011 31059           0.0      0.0      0.0  0.000000      0.0  0.000000   
           31060           0.0      0.0      0.0  0.000000      0.0  0.000000   
           31061           0.0      0.0      0.0  0.000000      0.0  0.000000   
           31062           0.0      0.0      0.0  0.000000      0.0  0.000000   
           31063           0.0      0.0      0.0  0.000000      0.0  0.000000   
...                        ...      ...      ...       ...      ...       ...   
D065626    39893           0.0      0.0      0.0  0.000000      0.0  0.000000   
           39894           0.0      0.0      0.0  0.000000      0.0  0.000000   
           39895           0.0      0.0      0.0  0.000000      0.0  0.000000   
           39896           0.0      0.0      0.0  0.000000      0.0  0.000000   
           47572           0.0      0.0      0.0  0.001802      0.0  0.001802   

ncbi_taxon_id          2304691   2304692   2529408  
disease    loaded_uid                               
D000067011 31059           0.0  0.000000  0.000000  
           31060           0.0  0.000000  0.000000  
           31061           0.0  0.003311  0.000000  
           31062           0.0  0.002563  0.000854  
           31063           0.0  0.002637  0.000000  
...                        ...       ...       ...  
D065626    39893           0.0  0.000000  0.000000  
           39894           0.0  0.000000  0.000000  
           39895           0.0  0.000000  0.000000  
           39896           0.0  0.000000  0.000000  
           47572           0.0  0.000000  0.000000  

[29963 rows x 1710 columns]

In [6]:
# SAVE AS NUMOPY ARRAY FOR BRAY-CURTIS DISTANCE CALCULATION
np.save("genus_data_pivot.npy", df_genus_pivot.values)


In [ ]:
# SAVE THE INDEX
pd.to_pickle(df_genus_pivot.index, "braycurtis_genus_index.pkl")


___
___

In [ ]:
# Step 1: Exclude unknown taxa
df_species_clean = df_species[df_species["ncbi_taxon_id"] != -1]

# Step 2: Keep only diseases with ≥ 30 samples
sample_counts = df_species_clean.groupby("disease")["loaded_uid"].nunique()
eligible_diseases = sample_counts[sample_counts >= 30].index.tolist()

df_species_filtered = df_species_clean[df_species_clean["disease"].isin(eligible_diseases)]

# Step 3: Count disease vs healthy samples
healthy_code = 'D006262'

num_healthy_samples = df_species_filtered[df_species_filtered["disease"] == healthy_code]["loaded_uid"].nunique()
num_disease_samples = df_species_filtered[df_species_filtered["disease"] != healthy_code]["loaded_uid"].nunique()

# Final summary
num_diseases = df_species_filtered["disease"].nunique()
num_samples = df_species_filtered["loaded_uid"].nunique()
num_taxa = df_species_filtered["ncbi_taxon_id"].nunique()

# Print
print(f"✅ Summary after filtering:")
print(f"- Unique diseases: {num_diseases}")
print(f"- Unique samples (loaded_uid): {num_samples}")
print(f"- Unique taxa (ncbi_taxon_id): {num_taxa}")
print(f"- Healthy samples (D006262): {num_healthy_samples}")
print(f"- Disease samples (excluding healthy): {num_disease_samples}")

# Optional: return the filtered DataFrame
df_species_filtered


✅ Summary after filtering:
- Unique diseases: 66
- Unique samples (loaded_uid): 26618
- Unique taxa (ncbi_taxon_id): 6971
- Healthy samples (D006262): 12485
- Disease samples (excluding healthy): 14152


loaded_uid  ncbi_taxon_id  relative_abundance  disease
1                 1            546             5.14775  D006262
2                 1            562            28.70520  D006262
3                 1            571             0.28295  D006262
4                 1            573             0.24973  D006262
5                 1            817            32.18570  D006262
...             ...            ...                 ...      ...
5225959       52859         357276             0.00913  D003093
5225960       52859         470565             0.02476  D003093
5225961       52859         649756             1.38735  D003093
5225962       52859         658089             0.17951  D003093
5225963       52859        1078480             0.35689  D003093

[5157360 rows x 4 columns]

In [10]:
# Check for duplicates across disease, loaded_uid, and ncbi_taxon_id

duplicates_species = df_species_filtered.duplicated(subset=["disease", "loaded_uid", "ncbi_taxon_id"])

# Count how many duplicates exist
num_duplicates_species = duplicates_species.sum()

# Display summary
if num_duplicates_species > 0:
    print(f"Found {num_duplicates_species} duplicate rows based on (disease, loaded_uid, ncbi_taxon_id).")
    display(df_genus_filtered[duplicates_species].head())
else:
    print("No duplicates found for (disease, loaded_uid, ncbi_taxon_id).")


No duplicates found for (disease, loaded_uid, ncbi_taxon_id).


In [12]:
# PIVOT THE TABLE FOR BRAY-CURTIS DISTANCE CALCULATION
# Step 1: Pivot to sample-by-taxon matrix
df_species_pivot = (
    df_species_filtered
    .pivot_table(
        index=["disease", "loaded_uid"],
        columns="ncbi_taxon_id",
        values="relative_abundance",
        aggfunc="sum",
        fill_value=0
    )
)
df_species_pivot

ncbi_taxon_id          7         9        11       14       17       19       \
disease    loaded_uid                                                          
D000067011 31059           0.0  0.000000      0.0      0.0      0.0  0.00000   
           31060           0.0  0.000000      0.0      0.0      0.0  0.00236   
           31061           0.0  0.003311      0.0      0.0      0.0  0.00000   
           31062           0.0  0.000000      0.0      0.0      0.0  0.00000   
           31063           0.0  0.000000      0.0      0.0      0.0  0.00000   
...                        ...       ...      ...      ...      ...      ...   
D065626    39893           0.0  0.000000      0.0      0.0      0.0  0.00000   
           39894           0.0  0.000000      0.0      0.0      0.0  0.00000   
           39895           0.0  0.000000      0.0      0.0      0.0  0.00000   
           39896           0.0  0.000000      0.0      0.0      0.0  0.00000   
           47572           0.0  0.000000      0.0      0.0      0.0  0.00000   

ncbi_taxon_id           24       25       33       34       ...  1935379  \
disease    loaded_uid                                       ...            
D000067011 31059       0.002325      0.0      0.0      0.0  ...      0.0   
           31060       0.000000      0.0      0.0      0.0  ...      0.0   
           31061       0.009933      0.0      0.0      0.0  ...      0.0   
           31062       0.001709      0.0      0.0      0.0  ...      0.0   
           31063       0.003956      0.0      0.0      0.0  ...      0.0   
...                         ...      ...      ...      ...  ...      ...   
D065626    39893       0.000000      0.0      0.0      0.0  ...      0.0   
           39894       0.000000      0.0      0.0      0.0  ...      0.0   
           39895       0.000000      0.0      0.0      0.0  ...      0.0   
           39896       0.000000      0.0      0.0      0.0  ...      0.0   
           47572       0.000000      0.0      0.0      0.0  ...      0.0   

ncbi_taxon_id          1936242  1937526  1938617  1945662  1955249  1977292  \
disease    loaded_uid                                                         
D000067011 31059           0.0      0.0      0.0      0.0      0.0      0.0   
           31060           0.0      0.0      0.0      0.0      0.0      0.0   
           31061           0.0      0.0      0.0      0.0      0.0      0.0   
           31062           0.0      0.0      0.0      0.0      0.0      0.0   
           31063           0.0      0.0      0.0      0.0      0.0      0.0   
...                        ...      ...      ...      ...      ...      ...   
D065626    39893           0.0      0.0      0.0      0.0      0.0      0.0   
           39894           0.0      0.0      0.0      0.0      0.0      0.0   
           39895           0.0      0.0      0.0      0.0      0.0      0.0   
           39896           0.0      0.0      0.0      0.0      0.0      0.0   
           47572           0.0      0.0      0.0      0.0      0.0      0.0   

ncbi_taxon_id          1985254  2093781  2339232  
disease    loaded_uid                             
D000067011 31059           0.0      0.0      0.0  
           31060           0.0      0.0      0.0  
           31061           0.0      0.0      0.0  
           31062           0.0      0.0      0.0  
           31063           0.0      0.0      0.0  
...                        ...      ...      ...  
D065626    39893           0.0      0.0      0.0  
           39894           0.0      0.0      0.0  
           39895           0.0      0.0      0.0  
           39896           0.0      0.0      0.0  
           47572           0.0      0.0      0.0  

[29963 rows x 6971 columns]

In [13]:
# SAVE AS NUMOPY ARRAY FOR BRAY-CURTIS DISTANCE CALCULATION
np.save("species_data_pivot.npy", df_species_pivot.values)

In [22]:
# SAVE THE INDEX
pd.to_pickle(df_species_pivot.index, "braycurtis_species_index.pkl")